In [1]:
import torch
import torch.autograd as autograd         # computation graph
from torch import Tensor                  # tensor node in the computation graph
import torch.nn as nn                     # neural networks
import torch.optim as optim               # optimizers e.g. gradient descent, ADAM, etc.

import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
from mpl_toolkits.axes_grid1 import make_axes_locatable
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.ticker
from torch.nn.parameter import Parameter

import numpy as np
import time
from pyDOE import lhs         #Latin Hypercube Sampling
import scipy.io

from smt.sampling_methods import LHS
from scipy.io import savemat

#Set default dtype to float32
torch.set_default_dtype(torch.float)

#PyTorch random number generator
torch.manual_seed(1234)

# Random number generators in other libraries
np.random.seed(1234)

# Device configuration
device = torch.device('cuda:3' if torch.cuda.is_available() else 'cpu')

print(device)

if device == 'cuda': 
    print(torch.cuda.get_device_name())

    

cuda:3


In [2]:
lr_tune = np.array([0.05,0.1,0.25,0.5,1]).reshape(-1,1)
n_value = np.array([1.0,3.0,5.0,8.0,10.0]).reshape(-1,1)
r_value = np.array([2,6,8]).reshape(-1,1)

LR_tune,N_value,R_value = np.meshgrid(lr_tune,n_value,r_value)

LR_tune = LR_tune.flatten('F').reshape(-1,1)
N_value = N_value.flatten('F').reshape(-1,1)
R_value = R_value.flatten('F').reshape(-1,1)


lrnr_tune = np.hstack((LR_tune,N_value,R_value))

In [3]:
def true_1D_1(x): #True function for 1D_1 dy2/dx2 + dy/dx - 6y = 0; BC1: y(0)=2; BC2: dy/dx at (x=0) = -1;
    y = np.exp(2*x) + np.exp(-3*x)
    return y
    

In [4]:
loss_thresh = 0.005

x = np.linspace(0,2,100).reshape(-1,1)

bc1_x = x[0].reshape(-1,1)
bc1_y = true_1D_1(x[0]).reshape(-1,1)
x_bc1_train = torch.from_numpy(bc1_x).float().to(device)
y_bc1_train = torch.from_numpy(bc1_y).float().to(device)
    

bc2_x = x[0].reshape(-1,1)
x_bc2_train = torch.from_numpy(bc2_x).float().to(device)
bc2_val = torch.tensor(-1.0,device=device)
bc2_val = bc2_val.view(1,1)

x_test = x.reshape(-1,1)
x_test_tensor = torch.from_numpy(x_test).float().to(device)
y_true = true_1D_1(x_test)
y_true_norm = np.linalg.norm(y_true,2)

# Domain bounds
lb = np.array(x[0]) 
ub = np.array(x[-1]) 

In [5]:
def colloc_pts(N_f,seed):
    #Collocation Points
    # Latin Hypercube sampling for collocation points 
    # N_f sets of tuples(x,y)
    x01 = np.array([[0.0, 1.0]])
    sampling = LHS(xlimits=x01,random_state =seed)
    
    x_coll_train = lb + (ub-lb)*sampling(N_f)
    x_coll_train = np.vstack((x_coll_train, bc1_x.reshape(-1,1))) # append training points to collocation points 

    return x_coll_train

In [6]:
class Sequentialmodel(nn.Module):
    
    def __init__(self,layers,n_val,rowdy_terms):
        super().__init__() #call __init__ from parent class 
              
    
        self.activation = nn.Tanh()
        self.loss_function = nn.MSELoss(reduction ='mean')
        
        'Initialise neural network as a list using nn.Modulelist'  
        self.linears = nn.ModuleList([nn.Linear(layers[i], layers[i+1]) for i in range(len(layers)-1)])
        
        for i in range(len(layers)-1):
            nn.init.xavier_normal_(self.linears[i].weight.data, gain=1.0)
            # set biases to zero
            nn.init.zeros_(self.linears[i].bias.data) 
        
        
        self.omega1 = Parameter(torch.ones((len(layers)-2,1))) 
        self.omega1.requiresGrad = True
        
        
        self.alpha = Parameter(torch.zeros(rowdy_terms,len(layers)-2))
        self.alpha.requiresGrad = True
        
        self.omega = Parameter((1/n_val)*torch.ones(rowdy_terms,len(layers)-2))
        self.omega.requiresGrad = True
        
        self.n = torch.tensor(n_val)
    
    'forward pass'
    def forward(self,x):
        if torch.is_tensor(x) != True:         
            x = torch.from_numpy(x)                
        
        u_b = torch.from_numpy(ub).float().to(device)
        l_b = torch.from_numpy(lb).float().to(device)
                      
        #preprocessing input 
        x = (x - l_b)/(u_b - l_b) #feature scaling
        
        #convert to float
        a = x.float()
        
        for i in range(len(layers)-2):
            z = self.linears[i](a)
            a = self.activation(self.omega1[i,0]*z)
            for j in range(rowdy_terms):
                a = a + self.alpha[j,i]*self.n*torch.sin((j+1)*self.n*self.omega[j,i]*z)
            
        a = self.linears[-1](a) 
         
        return a
                        
    def loss_BC1(self,x,y):
                
        loss_bc1 = self.loss_function(self.forward(x), y)
                
        return loss_bc1
    
    def loss_BC2(self,x_bc2,bc2_val):
        g = x_bc2.clone()             
        g.requires_grad = True
        y = self.forward(g)    
            
        y_x = autograd.grad(y,g,torch.ones([x_bc2.shape[0], 1]).to(device), retain_graph=True, create_graph=True,allow_unused = True)[0]
        
        dy_dx = y_x[:,[0]]
        
        bc2 = dy_dx
        
        loss_bc2= self.loss_function(bc2,bc2_val)

        return loss_bc2
    
    def loss_PDE(self, x_coll,f_hat):
             
        g = x_coll.clone()             
        g.requires_grad = True
  
        y = self.forward(g) 

        y_x = autograd.grad(y,g,torch.ones([x_coll.shape[0], 1]).to(device), retain_graph=True, create_graph=True,allow_unused = True)[0]
        y_xx = autograd.grad(y_x,g,torch.ones(x_coll.shape).to(device), create_graph=True,allow_unused = True)[0]

        dy_dx = y_x[:,[0]]
        
        dy2_d2x = y_xx[:,[0]]
        
        f = dy2_d2x + dy_dx - 6*y
        
        loss_f = self.loss_function(f,f_hat)
                
        return loss_f
    
    
    def loss(self,x_bc1,y_bc1,x_bc2,bc2_val,x_coll,f_hat):

        loss_bc1 = self.loss_BC1(x_bc1,y_bc1)
        loss_bc2 = self.loss_BC2(x_bc2,bc2_val)
        loss_f = self.loss_PDE(x_coll,f_hat)
        
        loss_val = loss_bc1 + loss_bc2 + loss_f
        
        return loss_val
          
    'test neural network'
    
    def test(self):
        y_pred = self.forward(x_test_tensor)
        y_pred = y_pred.cpu().detach().numpy()

        return y_pred
    
    def test_loss(self):
        y_pred = self.test()
        
        test_mse = np.mean(np.square(y_pred.reshape(-1,1) - y_true.reshape(-1,1)))
        test_re = np.linalg.norm(y_pred.reshape(-1,1) - y_true.reshape(-1,1),2)/y_true_norm
        
        return test_mse, test_re

In [7]:
def train_step(x_coll,f_hat):
    def closure():
        optimizer.zero_grad()
        loss = PINN.loss(x_bc1_train,y_bc1_train,x_bc2_train,bc2_val,x_coll,f_hat)
        loss.backward()
        
        return loss

    optimizer.step(closure)

In [8]:
def data_update(loss_np):
    train_loss.append(loss_np)
    alpha_val.append(PINN.alpha.cpu().detach().numpy())
    omega_val.append(PINN.omega.cpu().detach().numpy())
    test_mse, test_re = PINN.test_loss()
    test_mse_loss.append(test_mse)
    test_re_loss.append(test_re)

In [9]:
def train_model(max_iter,rep):
    print(rep) 
    torch.manual_seed(rep*123)
    start_time = time.time()
    thresh_flag = 0
    nan_flag = 0
    for i in range(max_iter):
        x_coll = torch.from_numpy(colloc_pts(N_f,i*11)).float().to(device)
        f_hat = torch.zeros(x_coll.shape[0],1).to(device)
        train_step(x_coll,f_hat)
        
        loss_np = PINN.loss(x_bc1_train,y_bc1_train,x_bc2_train,bc2_val,x_coll,f_hat).cpu().detach().numpy()
        if(thresh_flag == 0):
            if(loss_np < loss_thresh):
                time_threshold[rep] = time.time() - start_time
                epoch_threshold[rep] = i+1            
                thresh_flag = 1       
        data_update(loss_np)
        print(i,"Train Loss",train_loss[-1],"Test MSE",test_mse_loss[-1],"Test RE",test_re_loss[-1])
        if(np.isnan(loss_np)):
            nan_flag =1
            print("NAN BREAK!")
            break
    
    elapsed_time[rep] = time.time() - start_time
    print('Training time: %.2f' % (elapsed_time[rep]))
    
    return nan_flag

In [10]:
nan_tune = []
for tune_reps in range(75):
    max_reps = 10
    max_iter = 100
    label = "1D_SODE_rowdy_tune"+str(tune_reps)

    N_f = 1000

    train_loss_full = []
    test_mse_full = []
    test_re_full = []
    alpha_full = []
    omega_full = []
    elapsed_time= np.zeros((max_reps,1))

    time_threshold = np.empty((max_reps,1))
    time_threshold[:] = np.nan
    epoch_threshold = max_iter*np.ones((max_reps,1))
    
    n_val = lrnr_tune[tune_reps,1]
    rowdy_terms = int(lrnr_tune[tune_reps,2])

    for reps in range(max_reps):

        train_loss = []
        test_mse_loss = []
        test_re_loss =[]
        alpha_val = []
        omega_val = []

        'Generate Training data'
        torch.manual_seed(reps*36)
         #Total number of collocation points 
        
        

        layers = np.array([1,50,50,50,50,50,50,50,50,50,1]) #9 hidden layers
        PINN = Sequentialmodel(layers,n_val,rowdy_terms)
        PINN.to(device)

        'Neural Network Summary'
        print(PINN)

        params = list(PINN.parameters())

        optimizer = torch.optim.LBFGS(PINN.parameters(), lr=lrnr_tune[tune_reps,0], 
                                  max_iter = 10, 
                                  max_eval = 15, 
                                  tolerance_grad = 1e-5, 
                                  tolerance_change = 1e-5, 
                                  history_size = 100, 
                                  line_search_fn = 'strong_wolfe')


        nan_flag = train_model(max_iter,reps)


        torch.save(PINN.state_dict(),label+'_'+str(reps)+'.pt')
        train_loss_full.append(train_loss)
        test_mse_full.append(test_mse_loss)
        test_re_full.append(test_re_loss)
        alpha_full.append(alpha_val)
        omega_full.append(omega_val) 
        
        if(nan_flag == 1):
            nan_tune.append(tune_reps)
            break

        print('Training time: %.2f' % (elapsed_time[reps]))

    mdic = {"train_loss": train_loss_full,"test_mse_loss": test_mse_full, "test_re_loss": test_re_full, "Time": elapsed_time, "alpha": alpha_full, "omega": omega_full, "label": label}
    savemat(label+'.mat', mdic)

Sequentialmodel(
  (activation): Tanh()
  (loss_function): MSELoss()
  (linears): ModuleList(
    (0): Linear(in_features=1, out_features=50, bias=True)
    (1): Linear(in_features=50, out_features=50, bias=True)
    (2): Linear(in_features=50, out_features=50, bias=True)
    (3): Linear(in_features=50, out_features=50, bias=True)
    (4): Linear(in_features=50, out_features=50, bias=True)
    (5): Linear(in_features=50, out_features=50, bias=True)
    (6): Linear(in_features=50, out_features=50, bias=True)
    (7): Linear(in_features=50, out_features=50, bias=True)
    (8): Linear(in_features=50, out_features=50, bias=True)
    (9): Linear(in_features=50, out_features=1, bias=True)
  )
)
0
0 Train Loss 4.35411 Test MSE 386.12551767125706 Test RE 1.0016749990929097
1 Train Loss 4.033991 Test MSE 388.6446665747328 Test RE 1.004937236383367
2 Train Loss 3.311204 Test MSE 387.2673727405252 Test RE 1.003154988474914
3 Train Loss 2.4173021 Test MSE 384.5932529169153 Test RE 0.99968554627843

97 Train Loss 2.3811476 Test MSE 383.7374391911702 Test RE 0.9985726548216121
98 Train Loss 2.3811476 Test MSE 383.7374391911702 Test RE 0.9985726548216121
99 Train Loss 2.3811476 Test MSE 383.7374391911702 Test RE 0.9985726548216121
Training time: 43.99
Training time: 43.99
Sequentialmodel(
  (activation): Tanh()
  (loss_function): MSELoss()
  (linears): ModuleList(
    (0): Linear(in_features=1, out_features=50, bias=True)
    (1): Linear(in_features=50, out_features=50, bias=True)
    (2): Linear(in_features=50, out_features=50, bias=True)
    (3): Linear(in_features=50, out_features=50, bias=True)
    (4): Linear(in_features=50, out_features=50, bias=True)
    (5): Linear(in_features=50, out_features=50, bias=True)
    (6): Linear(in_features=50, out_features=50, bias=True)
    (7): Linear(in_features=50, out_features=50, bias=True)
    (8): Linear(in_features=50, out_features=50, bias=True)
    (9): Linear(in_features=50, out_features=1, bias=True)
  )
)
1
0 Train Loss 4.3321486 T

92 Train Loss 2.3810992 Test MSE 383.73716924099585 Test RE 0.9985723035854777
93 Train Loss 2.3810992 Test MSE 383.73716924099585 Test RE 0.9985723035854777
94 Train Loss 2.3810992 Test MSE 383.73716924099585 Test RE 0.9985723035854777
95 Train Loss 2.3810992 Test MSE 383.73716924099585 Test RE 0.9985723035854777
96 Train Loss 2.3810992 Test MSE 383.73716924099585 Test RE 0.9985723035854777
97 Train Loss 2.3810992 Test MSE 383.73716924099585 Test RE 0.9985723035854777
98 Train Loss 2.3810992 Test MSE 383.73716924099585 Test RE 0.9985723035854777
99 Train Loss 2.3810992 Test MSE 383.73716924099585 Test RE 0.9985723035854777
Training time: 19.22
Training time: 19.22
Sequentialmodel(
  (activation): Tanh()
  (loss_function): MSELoss()
  (linears): ModuleList(
    (0): Linear(in_features=1, out_features=50, bias=True)
    (1): Linear(in_features=50, out_features=50, bias=True)
    (2): Linear(in_features=50, out_features=50, bias=True)
    (3): Linear(in_features=50, out_features=50, bias

89 Train Loss 2.380828 Test MSE 383.6570642252786 Test RE 0.9984680723154479
90 Train Loss 2.380828 Test MSE 383.6570642252786 Test RE 0.9984680723154479
91 Train Loss 2.380828 Test MSE 383.6570642252786 Test RE 0.9984680723154479
92 Train Loss 2.380828 Test MSE 383.6570642252786 Test RE 0.9984680723154479
93 Train Loss 2.380828 Test MSE 383.6570642252786 Test RE 0.9984680723154479
94 Train Loss 2.380828 Test MSE 383.6570642252786 Test RE 0.9984680723154479
95 Train Loss 2.380828 Test MSE 383.6570642252786 Test RE 0.9984680723154479
96 Train Loss 2.380828 Test MSE 383.6570642252786 Test RE 0.9984680723154479
97 Train Loss 2.380828 Test MSE 383.6570642252786 Test RE 0.9984680723154479
98 Train Loss 2.380828 Test MSE 383.6570642252786 Test RE 0.9984680723154479
99 Train Loss 2.380828 Test MSE 383.6570642252786 Test RE 0.9984680723154479
Training time: 17.97
Training time: 17.97
Sequentialmodel(
  (activation): Tanh()
  (loss_function): MSELoss()
  (linears): ModuleList(
    (0): Linear(i

85 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.9984219432213688
86 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.9984219432213688
87 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.9984219432213688
88 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.9984219432213688
89 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.9984219432213688
90 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.9984219432213688
91 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.9984219432213688
92 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.9984219432213688
93 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.9984219432213688
94 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.9984219432213688
95 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.9984219432213688
96 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.9984219432213688
97 Train Loss 2.3806283 Test MSE 383.6216152319988 Test RE 0.998

...

13 Train Loss 2.3369489 Test MSE 374.95626794108796 Test RE 0.9870812251588233
14 Train Loss 2.319778 Test MSE 371.872175630556 Test RE 0.9830133702523264
15 Train Loss 2.2747135 Test MSE 363.6946802688906 Test RE 0.9721450225258209
16 Train Loss 2.2581797 Test MSE 359.76929744348854 Test RE 0.9668845743680174
17 Train Loss 2.2104688 Test MSE 354.23347548129726 Test RE 0.9594169405603822
18 Train Loss 2.1547554 Test MSE 345.2763037303391 Test RE 0.9472093348688574
19 Train Loss 2.1283362 Test MSE 337.49802728631124 Test RE 0.9364793425296012
20 Train Loss 2.090563 Test MSE 332.5168790962782 Test RE 0.9295428836669093
21 Train Loss 2.0686111 Test MSE 330.8293841809993 Test RE 0.927181207943175
22 Train Loss 2.013903 Test MSE 320.07968556344326 Test RE 0.9119932803026889
23 Train Loss 1.9877602 Test MSE 314.77613142858695 Test RE 0.9044060926079383
24 Train Loss 1.9457686 Test MSE 310.61029986137487 Test RE 0.8984015839834014
25 Train Loss 1.911676 Test MSE 304.5815052919275 Test RE 0.88

9 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980765634086053
10 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980765634086053
11 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980765634086053
12 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980765634086053
13 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980765634086053
14 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980765634086053
15 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980765634086053
16 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980765634086053
17 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980765634086053
18 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980765634086053
19 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980765634086053
20 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980765634086053
21 Train Loss 4.891892 Test MSE 383.35625198392654 Test RE 0.9980

5 Train Loss 2.3860376 Test MSE 384.01273048133413 Test RE 0.9989307760803219
6 Train Loss 2.3817048 Test MSE 383.41843790293285 Test RE 0.9981575113404629
7 Train Loss 2.3796966 Test MSE 383.3518767151987 Test RE 0.998070867837432
8 Train Loss 2.3774762 Test MSE 382.9812397321767 Test RE 0.9975882675762204
9 Train Loss 2.3756573 Test MSE 382.8442722933768 Test RE 0.9974098654581224
10 Train Loss 2.3744786 Test MSE 382.6354513664564 Test RE 0.9971378116795557
11 Train Loss 2.3735745 Test MSE 382.39107576400403 Test RE 0.9968193426618118
12 Train Loss 2.3734019 Test MSE 382.32774193370165 Test RE 0.9967367897396905
13 Train Loss 2.3709 Test MSE 381.8067813167304 Test RE 0.9960574803893661
14 Train Loss 2.3685014 Test MSE 381.44656327749914 Test RE 0.9955875011255237
15 Train Loss 2.3637965 Test MSE 380.1237387654629 Test RE 0.993859695107802
16 Train Loss 2.3578367 Test MSE 378.7599135143071 Test RE 0.992075185508661
17 Train Loss 2.3524215 Test MSE 378.09968709965955 Test RE 0.99121015

0 Train Loss 4.5449953 Test MSE 384.98232324550355 Test RE 1.0001910799322522
1 Train Loss 3.340295 Test MSE 383.48847664250883 Test RE 0.9982486734948957
2 Train Loss 2.7332819 Test MSE 383.8260717021567 Test RE 0.9986879692042526
3 Train Loss 2.412142 Test MSE 384.004926321936 Test RE 0.9989206255644743
4 Train Loss 2.385699 Test MSE 383.73102655306616 Test RE 0.9985643112106501
5 Train Loss 2.3831575 Test MSE 383.2463333108366 Test RE 0.9979334652902548
6 Train Loss 2.3812854 Test MSE 383.00528957658054 Test RE 0.9976195895621127
7 Train Loss 2.3812854 Test MSE 383.00528957658054 Test RE 0.9976195895621127
8 Train Loss 2.3812854 Test MSE 383.00528957658054 Test RE 0.9976195895621127
9 Train Loss 2.3812854 Test MSE 383.00528957658054 Test RE 0.9976195895621127
10 Train Loss 2.3812854 Test MSE 383.00528957658054 Test RE 0.9976195895621127
11 Train Loss nan Test MSE nan Test RE nan
12 Train Loss nan Test MSE nan Test RE nan
13 Train Loss nan Test MSE nan Test RE nan
14 Train Loss nan T

36 Train Loss 0.6331246 Test MSE 93.2981535402348 Test RE 0.49237852941720917
37 Train Loss 0.61554086 Test MSE 87.10598483882995 Test RE 0.4757585262663901
38 Train Loss 0.59145033 Test MSE 85.91276581718888 Test RE 0.4724887069968237
39 Train Loss 0.5675149 Test MSE 81.9754025622477 Test RE 0.4615347031884832
40 Train Loss 0.5567354 Test MSE 80.20975537408174 Test RE 0.45653720791472285
41 Train Loss 0.5240743 Test MSE 74.71582706488527 Test RE 0.44062474869654333
42 Train Loss 0.47846636 Test MSE 67.93599166635748 Test RE 0.4201579081040213
43 Train Loss 0.45002064 Test MSE 62.581768540937695 Test RE 0.40326125608413926
44 Train Loss 0.44708335 Test MSE 61.14480135837684 Test RE 0.3986046417473728
45 Train Loss 0.44029266 Test MSE 61.95210839178827 Test RE 0.4012274411773914
46 Train Loss 0.43206125 Test MSE 61.18361230226384 Test RE 0.3987311264846985
47 Train Loss 0.42740244 Test MSE 61.100897002197236 Test RE 0.39846150919634027
48 Train Loss 0.4215636 Test MSE 61.52372477986059 

In [11]:
lrnr_tune[tune_reps,2]

8.0

In [12]:
import scipy.io as sio

In [13]:
for tune_reps in range(75):
    label = "1D_SODE_rowdy_tune"+str(tune_reps)+".mat" #WRONGLY SAVED AS STAN - DOESN'T MATTER
    data = sio.loadmat(label)
    re = np.array(data["test_re_loss"])
    print(np.mean(re[:,-1]))

0.9985827750291165
0.9796249690709959
0.8270739933974871
0.3370447975474903
0.3773328804977455
0.9986422032465851
0.9483397037187847
0.9163521452940978
0.6206473008861497
0.4876659147239414
0.8761350178509979
nan
0.6316384285919876
nan
nan
0.8825438024760055
nan
nan
nan
nan
nan
nan
nan
nan
nan
0.9986190295650411
0.5262834920341072
0.4552126611665693
0.5742677197096948
0.7424235739503
0.998612779585342
0.46676846734699345
0.49486148274630326
nan
0.734962707628309
0.9340999494974987
0.3304694788831412
nan
nan
nan
nan
nan
nan
nan
0.6529301870525988
nan
nan
nan
nan
nan
0.9673237962238772
0.5248288791720428
0.6191621435914249
0.7369331293439327
0.803991390260489
0.9985461814165306
0.42918332164895334
0.6448519898043541
0.7176254580166981
0.8629760540388765
nan
nan
0.4172108931321773
nan
0.8055145043179485
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
